In [1]:
# Last amended: 12th July, 2020
# My folder: E:\OneDrive\Documents\maps\restaurants
# Ref: 
#       1.Folium Quickstart
#             https://python-visualization.github.io/folium/quickstart.html
#             https://python-graph-gallery.com/312-add-markers-on-folium-map/
#             https://python-graph-gallery.com/292-choropleth-map-with-folium/

#       2.ZOMATO INDIA DATA SET
#             https://www.kaggle.com/ronidas39/zomato-india-data-set
#       3.Zomato Restaurants Data of World Cities
#             https://www.kaggle.com/shrutimehta/zomato-restaurants-data
#       4.Delhi Neighborhood Data
#             https://www.kaggle.com/shaswatd673/delhi-neighborhood-data
#       5.Kaggle: Learn Geospatial Analysis
#             https://www.kaggle.com/learn/geospatial-analysis
#       6. Shapely user manual
#             https://shapely.readthedocs.io/en/stable/manual.html#the-shapely-user-manual
#       7. GeoPandas 101: Plot any data with a latitude and longitude on a map
#             https://towardsdatascience.com/geopandas-101-plot-any-data-with-a-latitude-and-longitude-on-a-map-98e01944b972
#

In [2]:
# 1.0 Call libraries
import pandas as pd
import numpy as np

# 1.1 Even though zomato data can be visualized
#     in multiple ways, we will confine ourselves
#     here to just map visualization
#import seaborn as sns

# 1.2 Folium uses Leaflet to plot interactive maps. Leaflet is the 
#     leading open-source JavaScript library for mobile-friendly
#      interactive maps.
# Install as: conda install -c conda-forge folium 
import folium
from folium import Choropleth, Circle, Marker
from folium.plugins import HeatMap, MarkerCluster

# 1.3 Geopandas makes working with and manipulating 
#      geospatial data very intutive. 
#       Install as: pip install geopandas
#        On ubuntu there is a problem in conda install
#        On Windows installations fail
import geopandas as gpd
import os

In [3]:

# 1.4 Display outputs from all commands in a cell
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [4]:
## 1.5 Set some options
pd.options.display.max_rows = 999

In [5]:
# 2.0 Set zomato data files path. There are 1308 files
#dir_path= "E:\\OneDrive\\Documents\\maps\\restaurants\\cities\\zomato_data\\delhi_ncr\\"
dir_path= "/home/ashok/Documents/maps/abcd/cities/delhi_ncr/"
delhiFiles = os.listdir(dir_path)
len(delhiFiles)   # 1308 files

1308

In [6]:
# 2.1 Sample reading and concatenating of two files.
df1 = pd.read_csv(dir_path + "1-Delhi NCRhotels.csv", sep = "|")
df2 = pd.read_csv(dir_path + "2-Delhi NCRhotels.csv", sep = "|")
pd.concat([df1,df2]).head(2)

NAME  PRICE                         CUSINE_CATEGORY  \
0  POMP - Pizza On My Plate    800  Pizza,Italian,Desserts,Burger,American   
1            Shawarma House    500             Healthy Food,Wraps,Lebanese   

        CITY                                 REGION  \
0  Delhi NCR                Greater Kailash 1 (GK1)   
1  Delhi NCR  Central Plaza Mall-- Golf Course Road   

                                                 URL  PAGE NO  CUSINE TYPE  \
0  https://www.zomato.com/ncr/pomp-pizza-on-my-pl...        1         none   
1  https://www.zomato.com/ncr/shawarma-house-golf...        1  Quick Bites   

                 TIMING RATING_TYPE RATING VOTES  
0  11am to 4am(Mon-Sun)   Excellent    4.6  1244  
1  11am to 4am(Mon-Sun)   Very Good    4.4  1408

In [7]:
# 2.2 Create an empty dataframe with onlu column names.
#     All zomato-delhi files will be concatenated to this
#     data frame:

zomato_delhi = pd.DataFrame(
                            columns= df1.columns.tolist()
                           )
# 2.2.1 Just check
zomato_delhi


Empty DataFrame
Columns: [NAME, PRICE, CUSINE_CATEGORY, CITY, REGION, URL, PAGE NO, CUSINE TYPE, TIMING, RATING_TYPE, RATING, VOTES]
Index: []

In [8]:
# 2.3 Concatenate all delhi files supplied by Zomato into a DataFrame
for i in delhiFiles:
    path = dir_path + i
    temp = pd.read_csv(path, sep = "|")
    zomato_delhi = pd.concat([zomato_delhi,temp])   

In [9]:
# 2.4
zomato_delhi.shape    # (19610,12)
zomato_delhi.dtypes   # All dtypes are 'object' types

(19610, 12)

NAME               object
PRICE              object
CUSINE_CATEGORY    object
CITY               object
REGION             object
URL                object
PAGE NO            object
CUSINE TYPE        object
TIMING             object
RATING_TYPE        object
RATING             object
VOTES              object
dtype: object

In [10]:
# 2.5 For convenience lowercase all column names and remove spaces

zomato_delhi.columns = [c.replace(" ","").lower()  for c in zomato_delhi.columns]

## Data cleaning
zomato data is unclean and has a number or problems. First, we need to clean this dataset.

In [11]:
# 3.0 Here is an indication of unclean data
#     Try to change 'price' to int
zomato_delhi["price"] = zomato_delhi["price"].astype('int32')

In [15]:
# 3.1 This gives error: could not convert string to float: '-'
zomato_delhi["rating"].astype("float64") 

ValueError: could not convert string to float: '-'

In [16]:
# 3.2 So let us search for all strings in this column
zomato_delhi["rating"].astype("str").sort_values()

7               -
3               -
7               -
6               -
5               -
         ...     
7         Opening
2         Opening
1         Opening
8         Opening
12    Temporarily
Name: rating, Length: 19610, dtype: object

In [17]:
# 3.4 Replace all three strings with value of 0:

zomato_delhi.loc[zomato_delhi["rating"] == "Opening", "rating" ] = 0
zomato_delhi.loc[zomato_delhi["rating"] == "Temporarily", "rating" ] = 0
zomato_delhi.loc[zomato_delhi["rating"] == "-", "rating" ] = 0

In [18]:
# 3.5 Any more string left?

zomato_delhi["rating"].astype("str").sort_values()

6       0
14      0
13      0
12      0
11      0
     ... 
6     NEW
5     NEW
4     NEW
1     NEW
14    NEW
Name: rating, Length: 19610, dtype: object

In [19]:
# 3.6 So replace this one also with 0:

zomato_delhi.loc[zomato_delhi["rating"] == "NEW", "rating" ] = 0

In [20]:
# 3.7 Any more left? All clear!
zomato_delhi["rating"].astype("str").sort_values()

14      0
9       0
12      0
0       0
3       0
     ... 
5     4.9
12    4.9
5     4.9
6     4.9
0     4.9
Name: rating, Length: 19610, dtype: object

In [21]:
# 3.8 So finally we perform dtype change on this column
zomato_delhi["rating"] = zomato_delhi["rating"].astype("float32")

In [22]:
# 4.0 Let us observe column: votes also
#     It also has strings
zomato_delhi["votes"].astype("str").sort_values()

3               -
13              -
14              -
8               -
14              -
         ...     
12        Opening
14        Opening
14        Opening
2         Opening
12    Temporarily
Name: votes, Length: 19610, dtype: object

In [23]:
# 4.1 This column also has many strings. So remove them also
zomato_delhi.loc[zomato_delhi["votes"] == "Temporarily", "votes" ] = 0
zomato_delhi.loc[zomato_delhi["votes"] == "-", "votes" ] = 0
zomato_delhi.loc[zomato_delhi["votes"] == "Opening", "votes" ] = 0
zomato_delhi.loc[zomato_delhi["votes"] == "NEW", "votes" ] = 0


In [24]:
# 4.2 Finally we change its dtype
zomato_delhi["votes"] = zomato_delhi["votes"].astype("int32")

## Other two datasets
We have two other datasets from Kaggle. These datasets record locational (latitude-longitude) information of various places and districts in Delhi. We will merge all three datasets in steps.

In [25]:
# 5.0 Read another two datasets also
#path_to_restdata= "E:\\OneDrive\\Documents\\maps\\restaurants\\"
path_to_locationaldata= "/home/ashok/Documents/maps/abcd/" 

# 5.1
delhi_location = pd.read_csv(path_to_locationaldata + "delhi_dataSet.csv")
delhi_res      = pd.read_csv(path_to_locationaldata + "restaurant_dataSet.csv")

# 5.2 It contains 'neighborhood' and within 'neighborhood',
#     'venue' wise locational data

delhi_res.head(2)

# 5.3 Dataset links names of 'neighborhood' to regions/districts
#      in Delhi

delhi_location.head(2)

sn  Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0   0  Adarsh Nagar              28.614193               77.071541   
1   1  Adarsh Nagar              28.614193               77.071541   

              Venue  Venue Latitude  Venue Longitude     Venue Category  
0  Eagle Boys Pizza       28.615595        77.070784        Pizza Place  
1       Bikanerwala       28.613391        77.076084  Indian Restaurant

sn           Borough  Neighborhood   latitude  longitude
0   0  North West Delhi  Adarsh Nagar  28.614192  77.071541
1   1  North West Delhi   Ashok Vihar  28.699453  77.184826

In [26]:
# 5.4 Change column names in delhi_res and in delhi_location 
#      to what is more conveient for us:

delhi_res.columns      = [c.replace(" ","_").lower() for c in delhi_res.columns]
delhi_location.columns = [c.lower() for c in delhi_location.columns]

# 5.5 Also change the column name 'borough' to 'DISTRICT'
delhi_location = delhi_location.rename(columns = {'borough' : "DISTRICT"})
delhi_location.head(2)

sn          DISTRICT  neighborhood   latitude  longitude
0   0  North West Delhi  Adarsh Nagar  28.614192  77.071541
1   1  North West Delhi   Ashok Vihar  28.699453  77.184826

In [27]:
# 5.6 So we have three datasets, as:

delhi_location.shape      # (185,5)
delhi_res.shape           # (849,8)
zomato_delhi.shape        # (19610,12)

(185, 5)

(849, 8)

(19610, 12)

## Merging datasets
We merge all three datasets

In [28]:
# 6.0 First, we merge the delhi_res and zomato_delhi datasets:

df = delhi_res.merge(zomato_delhi, how = "inner" , left_on = "neighborhood", right_on="region" )
df.head(2)
df.shape    # (40404, 20)

sn neighborhood  neighborhood_latitude  neighborhood_longitude     venue  \
0   8      Azadpur              28.707657               77.175547  jungrele   
1   8      Azadpur              28.707657               77.175547  jungrele   

   venue_latitude  venue_longitude          venue_category  \
0       28.705655        77.172069  Argentinian Restaurant   
1       28.705655        77.172069  Argentinian Restaurant   

                 name  price  cusine_category       city   region  \
0  The Crunchy Burger    250        Fast Food  Delhi NCR  Azadpur   
1         Pizza Kraft    500  Pizza,Fast Food  Delhi NCR  Azadpur   

                                                 url pageno   cusinetype  \
0  https://www.zomato.com/ncr/the-crunchy-burger-...    591  Quick Bites   
1  https://www.zomato.com/ncr/pizza-kraft-azadpur...    653  Quick Bites   

                  timing rating_type  rating  votes  
0  11am to 10pm(Mon-Sun)     Average     3.4     43  
1  11am to 11pm(Mon-Sun)   Not rated     0.0      0

(40404, 20)

In [29]:
# 6.1 Let us now see what all neighbourhoods occur in our dataset

df['neighborhood'].nunique()        # 60 of them
df['neighborhood'].value_counts()

60

Connaught Place       6693
Malviya Nagar         2208
Hauz Khas Village     1849
Vasant Kunj           1768
Janakpuri             1704
Kamla Nagar           1639
Shahdara              1308
Karol Bagh            1176
Laxmi Nagar           1158
Saket                  972
Defence Colony         969
Green Park             960
Punjabi Bagh           920
Mahipalpur             917
Paharganj              872
Krishna Nagar          868
Rajouri Garden         860
Tilak Nagar            815
Khan Market            792
Vikaspuri              748
Jangpura               728
East of Kailash        602
Nehru Place            600
Hauz Khas              582
Azadpur                552
Shakarpur              532
Moti Nagar             474
Paschim Vihar          452
Vasant Vihar           450
Shahpur Jat            448
Dilshad Garden         440
Jasola                 396
Vasundhara Enclave     388
Chittaranjan Park      385
Kirti Nagar            327
Naraina                324
Munirka                310
S

## Plotting data
For this notebook, we will just confine ourselves to area around Connaught place. There are many ways maps can be plotted. OF these, 'folium' is the least complicated.

In [30]:
# 7.0 Let us get mean of neighborhood latitude and neighborhood longitude for Connaught Place
lat_conn = df.loc[df['neighborhood'] == 'Connaught Place', "neighborhood_latitude"].mean()
long_conn = df.loc[df['neighborhood'] == 'Connaught Place', "neighborhood_longitude"].mean()


In [31]:
# 7.1 Center the map on these lat,long
map1 = folium.Map(
                  location=[lat_conn,long_conn],       # Map is centered at this location
                  tiles='openstreetmap',               # We will experiment with various tiles
                                                       # 'openstreetmap' is the default tile
                  zoom_start=20                        # Starting zoom level
                  )

In [32]:
# 7.2 Plot the map now
map1

In [33]:
# 7.3 Save this map to a file.
#     It will be saved to current folder
#     Open it in a separate browser tab

map1.save("myFirstmap.html")

## <a href=https://en.wikipedia.org/wiki/Tiled_web_map>What is a tile:</a><br>
    Tile map (raster or vector) is a map displayed in a browser by seamlessly joining dozens of individually requested image or vector data files over the Internet. It is the most popular way to display and navigate maps, replacing other methods such as WMS which typically display a single large image, with arrow buttons to navigate to nearby areas. Google Maps was one of the first major mapping sites to use this technique. The first tiled web maps used raster (image) tiles, before the emergence of vector tiles. Tiled web maps are normally displayed with no gap between tiles.
### Experiments with tiles<br>
    Default tile in folium is set to 'openstreetmap'. There are others available. Let us try them, one by one.

In [34]:
# 7.4 Try 'Stamen Terrain' tile
map2 = folium.Map(
                  location=[lat_conn,long_conn],      # Try this: [45.372, -121.6972]
                  tiles='Stamen Terrain',             # We will experiment with various tiles
                  zoom_start=12                       # To watch terrain, zoom level should be low
                  )

In [35]:
map2

In [36]:
# 7.5 Try 'Stamen Toner' tile
map3 = folium.Map(
                  location=[lat_conn,long_conn],       # Map is centered at this location
                  tiles='Stamen Toner',               # We will experiment with various tiles
                  zoom_start=20                        # Starting zoom level
                  )

In [37]:
map3

In [38]:
# 7.6 Try 'Stamen Terrain' tile for Mt Everest

map4 = folium.Map(
                  location=  [27.9881, 86.9250],
                   zoom_start=12,
                   tiles='Stamen Terrain'
                 )

map4

In [39]:
# 7.7 Try cartodbpositron tile:

map5 = folium.Map(
                  location=[lat_conn,long_conn],
                  tiles='cartodbpositron',
                  zoom_start=17
                 )

In [40]:
map5

## <a href=https://developers.google.com/maps/documentation/javascript/markers>Markers on map</a>
    A marker identifies a location on a map. By default, a marker uses a standard image. Markers can display custom images, in which case they are usually referred to as "icons". Markers and icons are objects of type Marker. Broadly speaking, markers are a type of overlay. 
    Markers are designed to be interactive. For example, by default they receive 'click' events, so you can add an event listener to bring up an info window displaying custom information. You can allow users to also move a marker on the map.

### High rated resturants

In [41]:

# 8.0 How many resturants have top-ratings
(df.rating == 4.9 ).sum()     # 69

69

In [42]:
df.head()

sn neighborhood  neighborhood_latitude  neighborhood_longitude     venue  \
0   8      Azadpur              28.707657               77.175547  jungrele   
1   8      Azadpur              28.707657               77.175547  jungrele   
2   8      Azadpur              28.707657               77.175547  jungrele   
3   8      Azadpur              28.707657               77.175547  jungrele   
4   8      Azadpur              28.707657               77.175547  jungrele   

   venue_latitude  venue_longitude          venue_category  \
0       28.705655        77.172069  Argentinian Restaurant   
1       28.705655        77.172069  Argentinian Restaurant   
2       28.705655        77.172069  Argentinian Restaurant   
3       28.705655        77.172069  Argentinian Restaurant   
4       28.705655        77.172069  Argentinian Restaurant   

                           name  price  \
0            The Crunchy Burger    250   
1                   Pizza Kraft    500   
2                  Fresh N Pure    300   
3  Guruji Appetizers and Bakers    250   
4                Banaras Sweets    450   

                                   cusine_category       city   region  \
0                                        Fast Food  Delhi NCR  Azadpur   
1                                  Pizza,Fast Food  Delhi NCR  Azadpur   
2  Fast Food,Burger,Rolls,Salad,Sandwich,Beverages  Delhi NCR  Azadpur   
3                                     North Indian  Delhi NCR  Azadpur   
4                                           Mithai  Delhi NCR  Azadpur   

                                                 url pageno   cusinetype  \
0  https://www.zomato.com/ncr/the-crunchy-burger-...    591  Quick Bites   
1  https://www.zomato.com/ncr/pizza-kraft-azadpur...    653  Quick Bites   
2  https://www.zomato.com/ncr/fresh-n-pure-azadpu...    285  Quick Bites   
3  https://www.zomato.com/ncr/guruji-appetizers-a...    912  Quick Bites   
4  https://www.zomato.com/ncr/banaras-sweets-azad...    912   Sweet Shop   

                  timing rating_type  rating  votes  
0  11am to 10pm(Mon-Sun)     Average     3.4     43  
1  11am to 11pm(Mon-Sun)   Not rated     0.0      0  
2  11am to 11pm(Mon-Sun)        Good     3.6     25  
3  11am to 11pm(Mon-Sun)     Average     2.9      6  
4  11am to 10pm(Mon-Sun)   Not rated     0.0      0

In [43]:
# 8.1 Get dataframe with rating: 4.9
temp = df.loc[df["rating"] == 4.9, ["venue_latitude","venue_longitude", "venue", "cusine_category"]]
temp.dtypes
temp.head()    # For almost all of them cusine_category is Biryani,North Indian

venue_latitude     float64
venue_longitude    float64
venue               object
cusine_category     object
dtype: object

venue_latitude  venue_longitude            venue       cusine_category
6715       28.629999        77.220401   Rajdhani Thali  Biryani,North Indian
6812       28.632581        77.221125       Farzi Cafe  Biryani,North Indian
6909       28.633412        77.218292         Wenger's  Biryani,North Indian
7006       28.631629        77.220364          Chaayos  Biryani,North Indian
7103       28.630253        77.220985  Barbeque Nation  Biryani,North Indian

In [44]:
# 8.2 
for idx,row in temp.iterrows():
    abc = Marker(
                    [
                        row['venue_latitude'],
                        row['venue_longitude']
                     ]
                 ).add_to(map5)

In [45]:
map5

In [46]:
# 8.3 Add a on-click popup to each marker
for idx,row in temp.iterrows():
    abc = Marker(
                    [
                        row['venue_latitude'],
                        row['venue_longitude'],
                        
                    ],
                    popup = row['venue'] + "; " + row["cusine_category"]
        
                 ).add_to(map5)

In [47]:
map5

### Get top-rated sweet shops

In [48]:
# 8.1 Get dataframe with rating: 4.9
temp = df.loc[(df["cusinetype"] == 'Sweet Shop') & (df["rating"] > 3.5), ["venue_latitude","venue_longitude", "venue", "cusine_category"]]
temp.head()   

venue_latitude  venue_longitude                        venue  \
579       28.644982        77.223504                          KFC   
586       28.644982        77.223504                          KFC   
616       28.641805        77.219091                          KFC   
623       28.641805        77.219091                          KFC   
653       28.642846        77.223038  Comesum - The Food Junction   

        cusine_category  
579  Mithai,Street Food  
586  Mithai,Street Food  
616  Mithai,Street Food  
623  Mithai,Street Food  
653  Mithai,Street Food

In [49]:
# 8.2 Get a map with marker for sweet shops

map6 = folium.Map(
                  location=[28.644982,77.223504],
                  tiles='cartodbpositron',
                  zoom_start=15
                 )

# 8.3 Another way to iterate over temp data

for i in range(0,len(temp)):
    abc=Marker(
                [
                  temp.iloc[i]['venue_latitude'],
                  temp.iloc[i]['venue_longitude']
                ] 
              ).add_to(map6)


map6

### Markers in a cluster

In [50]:
# 9.0 Get dataframe with rating <= 3.0

temp = df.loc[df["rating"] <= 3.0, ["venue_latitude","venue_longitude"]]
temp.head()

venue_latitude  venue_longitude
1       28.705655        77.172069
3       28.705655        77.172069
4       28.705655        77.172069
6       28.705655        77.172069
7       28.705655        77.172069

In [51]:
# 9.1 Create the map
map7 = folium.Map(
                   location=[lat_conn,long_conn],
                   tiles='cartodbpositron',
                   zoom_start=13
                  )




In [52]:
## Generate Marker clusters

# 9.2 Create an empty Marker cluster
mc = MarkerCluster()# Create the map

# 9.3 Iterate over the dataframe
#     And add 'marker' to marker-cluster
for idx, row in temp.iterrows():
     abc = mc.add_child(
                         Marker(
                                 [row['venue_latitude'], row['venue_longitude']]
                                )
                        )
        

In [53]:
# 9.4 Overlay marker-cluster to map
#     and display map
map7.add_child(mc)

### Heat maps
    A heatmap is a visualization used to depict the intensity of data at geographical points. When the Heatmap Layer is enabled, a colored overlay will appear on top of the map. By default, areas of higher intensity will be colored red, and areas of lower intensity will appear green.

In [54]:
# 10. Create a base map
map8 = folium.Map(
                    location=[lat_conn,long_conn],
                    tiles='cartodbpositron',
                    zoom_start=11
                  )

# 10.1 Add a heatmap to the base map
HeatMap(
        data= df[['venue_latitude', 'venue_longitude']],
        radius=15
       ).add_to(map8)

# 10.2 Display the map
map8

## Choropleth map?
From Wikipedia<br>
<blockquote>
    A choropleth map (from Greek χῶρος "area/region" and πλῆθος "multitude") is a type of thematic map in which areas are shaded or patterned in proportion to a statistical variable that represents an aggregate summary of a geographic characteristic within each area, such as population density or per-capita income.

Choropleth maps provide an easy way to visualize how a measurement varies across a geographic area or show the level of variability within a region. A heat map or isarithmic map is similar but does not use a priori geographic areas. They are the most common type of thematic map because published statistical data (from government or other sources) is generally aggregated into well-known geographic units, such as countries, states, provinces, and counties, and thus they are relatively easy to create using GIS, spreadsheets, or other software tools. </blockquote><br>
<img src=https://datavizcatalogue.com/methods/images/top_images/choropleth.png width=500 height =500 />

<br>Ref: See <a href = https://python-graph-gallery.com/292-choropleth-map-with-folium/>this page on how to draw choropleth map with folium</a>


In [55]:
# 11.0 Read delhi-shape file

districts_all = gpd.read_file('/home/ashok/Documents/maps/abcd/delhi/Districts.shp')

In [56]:
# 11.1 It is a small dataset
districts_all

OBJECTID    DISTRICT                  STATE  \
0        99     Central  Nation Capital Region   
1       167        East  Nation Capital Region   
2       417  North East  Nation Capital Region   
3       413       North  Nation Capital Region   
4       420  North West  Nation Capital Region   
5       411   New Delhi  Nation Capital Region   
6       544       South  Nation Capital Region   
7       550  South West  Nation Capital Region   
8       613        West  Nation Capital Region   

                                            geometry  
0  POLYGON ((77.26042 28.62286, 77.25705 28.62268...  
1  POLYGON ((77.30482 28.57678, 77.29593 28.58194...  
2  POLYGON ((77.25066 28.66244, 77.25021 28.66266...  
3  POLYGON ((77.21434 28.78352, 77.21329 28.78031...  
4  POLYGON ((77.17093 28.66833, 77.16689 28.67303...  
5  POLYGON ((77.26042 28.62286, 77.26267 28.62114...  
6  POLYGON ((77.26455 28.60747, 77.26558 28.60738...  
7  POLYGON ((77.18253 28.64817, 77.18380 28.64638...  
8  POLYGON ((77.17093 28.66833, 77.17072 28.66817...

In [57]:
# 11.2 We are interested in only two columns; make on of them as index

districts = districts_all[["DISTRICT", "geometry"]].set_index("DISTRICT")
districts

geometry
DISTRICT                                                     
Central     POLYGON ((77.26042 28.62286, 77.25705 28.62268...
East        POLYGON ((77.30482 28.57678, 77.29593 28.58194...
North East  POLYGON ((77.25066 28.66244, 77.25021 28.66266...
North       POLYGON ((77.21434 28.78352, 77.21329 28.78031...
North West  POLYGON ((77.17093 28.66833, 77.16689 28.67303...
New Delhi   POLYGON ((77.26042 28.62286, 77.26267 28.62114...
South       POLYGON ((77.26455 28.60747, 77.26558 28.60738...
South West  POLYGON ((77.18253 28.64817, 77.18380 28.64638...
West        POLYGON ((77.17093 28.66833, 77.17072 28.66817...

In [58]:
# 11.3 Read another delhi raelated data

delhi_location = pd.read_csv("/home/ashok/Documents/maps/abcd/" + "delhi_dataSet.csv")
delhi_location.columns = [c.lower() for c in delhi_location.columns]

In [59]:
# 11.4

delhi_location = delhi_location.rename(columns = {'borough' : "DISTRICT"})
delhi_location.head()

sn          DISTRICT  neighborhood   latitude  longitude
0   0  North West Delhi  Adarsh Nagar  28.614192  77.071541
1   1  North West Delhi   Ashok Vihar  28.699453  77.184826
2   2  North West Delhi       Azadpur  28.707657  77.175547
3   3  North West Delhi        Bawana  28.799660  77.032885
4   4  North West Delhi     Begum Pur        NaN        NaN

In [60]:
# 11.5 How many times various districts occur in this data:

delhi_location['DISTRICT'].value_counts()


South Delhi         49
North Delhi         27
South West Delhi    21
West Delhi          20
East Delhi          19
North West Delhi    18
North East Delhi    13
New Delhi           10
Central Delhi        8
Name: DISTRICT, dtype: int64

In [61]:
# 11.6 Names of Dictrict should match in both delhi_location and districts DataFrames

delhi_location.loc[delhi_location['DISTRICT'] == 'South Delhi', "DISTRICT"] = 'South'
delhi_location.loc[delhi_location['DISTRICT'] == 'North Delhi', "DISTRICT"] = 'North'
delhi_location.loc[delhi_location['DISTRICT'] == 'West Delhi', "DISTRICT"] = 'West'
delhi_location.loc[delhi_location['DISTRICT'] == 'East Delhi', "DISTRICT"] = 'East'
delhi_location.loc[delhi_location['DISTRICT'] == 'Central Delhi', "DISTRICT"] = 'Central'
delhi_location.loc[delhi_location['DISTRICT'] == 'North East Delhi', "DISTRICT"] = 'North East'
delhi_location.loc[delhi_location['DISTRICT'] == 'North West Delhi', "DISTRICT"] = 'North West'
delhi_location.loc[delhi_location['DISTRICT'] == 'South West Delhi', "DISTRICT"] = 'South West'
delhi_location['DISTRICT'].value_counts()


South         49
North         27
South West    21
West          20
East          19
North West    18
North East    13
New Delhi     10
Central        8
Name: DISTRICT, dtype: int64

In [62]:
# 11.7 Merge delhi_location first with df.
df = delhi_location.merge(df, how = "inner" , on = "neighborhood" )
df.shape
df.head()

(43096, 24)

sn_x    DISTRICT neighborhood   latitude  longitude  sn_y  \
0     2  North West      Azadpur  28.707657  77.175547     8   
1     2  North West      Azadpur  28.707657  77.175547     8   
2     2  North West      Azadpur  28.707657  77.175547     8   
3     2  North West      Azadpur  28.707657  77.175547     8   
4     2  North West      Azadpur  28.707657  77.175547     8   

   neighborhood_latitude  neighborhood_longitude     venue  venue_latitude  \
0              28.707657               77.175547  jungrele       28.705655   
1              28.707657               77.175547  jungrele       28.705655   
2              28.707657               77.175547  jungrele       28.705655   
3              28.707657               77.175547  jungrele       28.705655   
4              28.707657               77.175547  jungrele       28.705655   

   ...                                  cusine_category       city   region  \
0  ...                                        Fast Food  Delhi NCR  Azadpur   
1  ...                                  Pizza,Fast Food  Delhi NCR  Azadpur   
2  ...  Fast Food,Burger,Rolls,Salad,Sandwich,Beverages  Delhi NCR  Azadpur   
3  ...                                     North Indian  Delhi NCR  Azadpur   
4  ...                                           Mithai  Delhi NCR  Azadpur   

                                                 url pageno   cusinetype  \
0  https://www.zomato.com/ncr/the-crunchy-burger-...    591  Quick Bites   
1  https://www.zomato.com/ncr/pizza-kraft-azadpur...    653  Quick Bites   
2  https://www.zomato.com/ncr/fresh-n-pure-azadpu...    285  Quick Bites   
3  https://www.zomato.com/ncr/guruji-appetizers-a...    912  Quick Bites   
4  https://www.zomato.com/ncr/banaras-sweets-azad...    912   Sweet Shop   

                  timing rating_type rating votes  
0  11am to 10pm(Mon-Sun)     Average    3.4    43  
1  11am to 11pm(Mon-Sun)   Not rated    0.0     0  
2  11am to 11pm(Mon-Sun)        Good    3.6    25  
3  11am to 11pm(Mon-Sun)     Average    2.9     6  
4  11am to 10pm(Mon-Sun)   Not rated    0.0     0  

[5 rows x 24 columns]

In [63]:
# 11.8
plot_dict = df['DISTRICT'].value_counts()
plot_dict

South         12215
New Delhi      7610
West           6300
East           5180
South West     4003
North          2996
Central        2492
North East     1748
North West      552
Name: DISTRICT, dtype: int64

In [64]:
# 11.9 Create a base map
map9 = folium.Map(
                   location=[lat_conn,long_conn],
                   tiles='cartodbpositron',
                   zoom_start=12
                 )

In [65]:
# 11.10
Choropleth(geo_data=districts.__geo_interface__, 
           data=plot_dict, 
           key_on="feature.id", 
           fill_color='YlGnBu', 
           #legend_name='some thing'
          ).add_to(map9)

In [66]:
map9

In [ ]:
# ToDO
#   Bubble maps with folium
#   https://python-graph-gallery.com/313-bubble-map-with-folium/

In [ ]:
###################### I am done ################